In [1]:
import warnings
warnings.filterwarnings('ignore')
import pandas as pd
import numpy as np
from pandas import DataFrame
from matplotlib import pyplot
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import precision_recall_fscore_support as score
import time
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import KFold, cross_val_score
from sklearn.ensemble import RandomForestClassifier,GradientBoostingClassifier
pd.set_option("display.max_colwidth",100)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
%matplotlib inline
import matplotlib.pyplot as plt

In [52]:
import os
os.getcwd()

'/Users/kumarkovid'

In [2]:
data=pd.read_csv("/Users/kumarkovid/Downloads/DS_Challenge_BDIPlus/complaints.csv")

In [3]:
data.drop(data.columns[0],axis=1,inplace=True)

In [4]:
useful_data = data[['Created Date','Closed Date','Location Type','Incident Zip','Incident Address','Due Date',
                    'Street Name','Cross Street 1','Cross Street 2', 'Address Type', 'City', 'Status',
                    'Community Board','Borough', 'Park Borough', 'Location','Descriptor']]

In [5]:
useful_data['Created Date'] = pd.to_datetime(useful_data['Created Date']) 
useful_data['Closed Date'] = pd.to_datetime(useful_data['Closed Date'])
useful_data['Due Date'] = pd.to_datetime(useful_data['Due Date'])

In [6]:
useful_data['Time Between Close'] = (useful_data['Closed Date'] - useful_data['Created Date']).dt.days
useful_data['Time to Due'] = (useful_data['Due Date'] - useful_data['Created Date']).dt.days
useful_data['Time to Close'] = (useful_data['Due Date'] - useful_data['Closed Date']).dt.days

In [7]:
useful_data['Created Date'] = pd.to_datetime(useful_data['Created Date']).dt.to_period('M')
useful_data['Closed Date'] = pd.to_datetime(useful_data['Closed Date']).dt.to_period('M')
useful_data['Due Date'] = pd.to_datetime(useful_data['Due Date']).dt.to_period('M')

In [8]:
useful_data

Created Date Closed Date                  Location Type  Incident Zip  \
0         2016-09     2016-09              Catch Basin/Sewer       10037.0   
1         2016-09     2017-01                     Vacant Lot           NaN   
2         2016-09     2016-09   3+ Family Mixed Use Building       11238.0   
3         2016-09     2016-09            1-2 Family Dwelling       11203.0   
4         2016-09     2016-09            1-2 Family Dwelling       11203.0   
5         2016-09     2016-09        3+ Family Apt. Building       10010.0   
6         2016-09     2016-09   3+ Family Mixed Use Building       10303.0   
7         2016-09     2016-09            1-2 Family Dwelling       10310.0   
8         2016-09     2016-09        3+ Family Apt. Building       11213.0   
9         2016-09     2016-09          Other (Explain Below)       11226.0   
10        2016-09     2016-09            1-2 Family Dwelling       11210.0   
11        2016-09     2016-09          Other (Explain Below)       10065.0   
12        2016-09     2016-09                Vacant Building       10314.0   
13        2016-09     2016-09            Commercial Building       10024.0   
14        2016-09     2016-09            1-2 Family Dwelling       11201.0   
15        2016-09     2016-09          Other (Explain Below)       11238.0   
16        2016-09     2016-09        3+ Family Apt. Building       10029.0   
17        2016-09     2016-09            1-2 Family Dwelling       11379.0   
18        2016-09     2016-09        3+ Family Apt. Building       11357.0   
19        2016-09     2016-10              Catch Basin/Sewer       11357.0   
20        2016-09     2016-09        3+ Family Apt. Building       11226.0   
21        2016-09     2016-09        3+ Family Apt. Building       11355.0   
22        2016-09     2016-09            Commercial Building       10452.0   
23        2016-09     2016-09  1-2 Family Mixed Use Building       10463.0   
24        2016-09     2016-09        3+ Family Apt. Building       10456.0   
25        2016-09     2016-10            1-2 Family Dwelling       10305.0   
26        2016-09     2016-09            1-2 Family Dwelling       10308.0   
27        2016-09     2016-09            Commercial Building       10001.0   
28        2016-09     2016-09          Other (Explain Below)       11433.0   
29        2016-09     2016-09          Other (Explain Below)       11379.0   
30        2016-09     2016-09          Other (Explain Below)       11206.0   
31        2016-09     2016-09        3+ Family Apt. Building       10462.0   
32        2016-09     2016-09        3+ Family Apt. Building       11217.0   
33        2016-09     2016-09            Commercial Building       11238.0   
34        2016-09     2016-09        3+ Family Apt. Building       11373.0   
35        2016-09     2016-09        3+ Family Apt. Building       11213.0   
36        2016-09     2016-09            Commercial Building       11379.0   
37        2016-09     2016-09            1-2 Family Dwelling       11232.0   
38        2016-09     2016-09            Commercial Building       11209.0   
39        2016-09     2016-09          Other (Explain Below)       10468.0   
40        2016-09     2016-09          Other (Explain Below)       11204.0   
41        2016-09     2016-11                     Vacant Lot       10306.0   
42        2016-09     2016-09              Construction Site       10024.0   
43        2016-09     2016-09            1-2 Family Dwelling       11379.0   
44        2016-09     2016-09        3+ Family Apt. Building       11372.0   
45        2016-09     2016-09            1-2 Family Dwelling       11207.0   
46        2016-09     2016-09        3+ Family Apt. Building       10452.0   
47        2016-09     2016-09            1-2 Family Dwelling       10470.0   
48        2016-09     2016-09        3+ Family Apt. Building       10036.0   
49        2016-09     2016-09        3+ Family Apt. Building       11207.0   
50        2016-09     2016-

In [9]:
useful_data = useful_data.drop(['Created Date', 'Closed Date', 'Due Date'], axis=1)

In [10]:
#useful_data_new = useful_data.dropna()
for column in useful_data.columns:
    useful_data[column].fillna(useful_data[column].mode()[0], inplace=True)

In [11]:
y = useful_data['Descriptor']
X = useful_data.drop('Descriptor',axis=1)
X = pd.get_dummies(X)
y = pd.DataFrame(y)

In [17]:
r = {'Rat Sighting': 0, 'Mouse Sighting':1, 'Condition Attracting Rodents':2, 'Signs of Rodents':3}
y = y.replace({"Descriptor": r})

In [18]:
X.shape

(3101, 8301)

In [19]:
y.shape

(3101, 1)

In [25]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [26]:
from sklearn.neighbors import KNeighborsClassifier
neigh = KNeighborsClassifier(n_neighbors=4)

In [27]:
neigh.fit(X_train, y_train)

KNeighborsClassifier(n_neighbors=4)

In [28]:
y_pred = neigh.predict(X_test)

In [29]:
from sklearn.metrics import accuracy_score
accuracy_score(y_test, y_pred)

0.5314009661835749

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X,y,test_size = 0.2, random_state = 42)

In [ ]:
print("Rows in X Train set:",len(X_train), "Rows in X Test set:", len(X_test))
print("Rows in y Train set:",len(y_train), "Rows in y Test set:", len(y_test))

In [30]:
rf=RandomForestClassifier(n_jobs=-1)
k_fold=KFold(n_splits=5)
cross_val_score(rf,X,y,cv=k_fold,scoring='accuracy',n_jobs=-1)

array([0.59903382, 0.59516129, 0.57580645, 0.60967742, 0.58387097])

In [31]:
rf=RandomForestClassifier(n_estimators=50, max_depth=20, n_jobs= -1)
rf_model=rf.fit(X_train,y_train)
sorted(zip(rf_model.feature_importances_,X_train.columns),reverse=True)[:10]

[(0.02536661910316919, 'Incident Zip'),
 (0.020675395644174026, 'Time to Close'),
 (0.018756083155109852, 'Location Type_3+ Family Apt. Building'),
 (0.018735203929702637, 'Time Between Close'),
 (0.014553399032984148, 'Cross Street 2_BEND'),
 (0.013573139562993537, 'Address Type_LATLONG'),
 (0.012770466315034274, 'Location Type_1-2 Family Dwelling'),
 (0.01117586266888831, 'Address Type_ADDRESS'),
 (0.010227470221043262, 'Location Type_Other (Explain Below)'),
 (0.008174220571951114, 'Street Name_EAST 30TH STREET')]

In [36]:
from sklearn.metrics import accuracy_score
accuracy_score(y_test, y_pred)

0.5314009661835749

In [39]:
X_train.shape

(2480, 8301)

In [40]:
y_train.shape

(2480, 1)

In [43]:
def train_RF(n_est,depth):
    rf=RandomForestClassifier(n_estimators=n_est,max_depth=depth,n_jobs=-1)
    rf_model=rf.fit(X_train,y_train)
    y_pred=rf_model.predict(X_test)
    print(accuracy_score(y_test, y_pred))
for n_est in [50,100,150,200]:
    for depth in [20,30,60, 90, None]:
        train_RF(n_est,depth)

0.5426731078904992
0.5555555555555556
0.5603864734299517
0.5619967793880838
0.5491143317230274
0.5426731078904992
0.5539452495974235
0.5684380032206119
0.5603864734299517
0.5539452495974235
0.5410628019323671
0.5507246376811594
0.5668276972624798
0.5571658615136876
0.5619967793880838
0.5394524959742351
0.5507246376811594
0.5700483091787439
0.5619967793880838
0.5603864734299517
